| ![EEW logo](https://github.com/edgi-govdata-archiving/EEW-Image-Assets/blob/master/Jupyter%20instructions/eew.jpg?raw=true) | ![EDGI logo](https://github.com/edgi-govdata-archiving/EEW-Image-Assets/blob/master/Jupyter%20instructions/edgi.png?raw=true) |
|---|---|

#### This notebook is licensed under GPL 3.0. Please visit our Github repo for more information: 
#### The notebook was collaboratively authored by the Environmental Data & Governance Initiative (EDGI) following our authorship protocol: https://docs.google.com/document/d/1CtDN5ZZ4Zv70fHiBTmWkDJ9mswEipX6eCYrwicP66Xw/
#### For more information about this project, visit https://www.environmentalenforcementwatch.org/

Here we load some helper code to get us going. If your environment already has these loaded this cell may be skipped. (If you're not sure, it's best to run this cell!)

In [1]:
# We have a folder of chunks of reusable code that we're using across different
#  Notebooks. This step goes and gets the relevant code from that folder so we
#  can use it here. (https://github.com/edgi-govdata-archiving/ECHO_modules/)
!git clone https://github.com/edgi-govdata-archiving/ECHO_modules.git -b reorganization &>/dev/null;

# Geopandas is an open source library for working with geographic data using the
#   data structures library "pandas" (common in Python for data processing).
#   (https://geopandas.org/)
!pip install geopandas  &>/dev/null;

# Topojson is an open source library that lets us keep file sizes small when
#   working with geographic data, so the Notebooks can run faster while still
#   working with detailed shapes. (https://github.com/mattijn/topojson)
!pip install topojson &>/dev/null;

# Install rtree to enable geopandas to clip data spatially
!pip install rtree &>/dev/null;

# Install a tool to help with Census data
#https://pypi.org/project/CensusData/ !!!!
!pip install censusdata &>/dev/null;
import censusdata 

import warnings
warnings.filterwarnings('ignore')

# This code block will print a lot of data as it fetches and installs the libraries
#   Specified above. When it's done, the line below lets us know by printing "Done!"
print("Done!")

Done!


This cell must be run to bring in some utility functions.

In [2]:
# These code blocks come from our folder (https://github.com/edgi-govdata-archiving/ECHO_modules/)
# Each of the files contains a series of function definitions. By running
#   those files here, we make the functions available in this Notebook.
%run ECHO_modules/utilities.py
%run ECHO_modules/presets.py
%run ECHO_modules/class.py
print("Done!")

Done!


# Analying Safe Drinking Water Act (SDWA) Data from Public Water Systems (PWS) and the Environmental Protection Agency (EPA)

## Get some basic information about New Jersey
We'll draw in some info about PWS across NJ to start. This may take a couple of minutes - hang tight!

In [3]:
nj = Echo(['NJ'], "States", ["SDWA Public Water Systems"])
print("Done!")

36144 program records were found
Done!


## Show Public Water Systems for a specific city
Let's look at which areas these PWS serve. First, run this cell to pick a specific area. You'll notice that the area names refer to township numbers (e.g. MOUNT OLIVE TWP.-1427). 

In [16]:
import ipywidgets as widgets

# Get the cities
areas = list(nj.results["SDWA Public Water Systems"]["CITY_SERVED"].unique())
areas = [str(a) for a in areas if a != "nan"]
areas.sort()

# Show a dropdown menu to select one.
pick_area = widgets.Dropdown(
    options=areas,
    description='Area:',
    disabled=False,
)
display(pick_area)

Dropdown(description='Area:', options=('ABERDEEN TWP-1330', 'ABSECON CITY-0101', 'ALEXANDRIA TWP.-1001', 'ALLA…

Now let's map the PWS serving the area you selected. 

On the map, orange circles = relative size of the water system serving the area, in terms of population. Black dots = other NJ PWS.

In [17]:
# Filter to specific city of interest
nj.results["SDWA Public Water Systems"] = nj.results["SDWA Public Water Systems"].loc[nj.results["SDWA Public Water Systems"]["CITY_SERVED"]==pick_area.value]
# Show the map
nj.show_program_map("SDWA Public Water Systems")

Are any of these PWS serious violators? We'll show which ones are and for what fiscal year.

In [27]:
# Add the Serious Violators data for all of NJ
nj.add("SDWA Serious Violators")

# Filter to just the area picked above
nj.results["SDWA Serious Violators"] = nj.results["SDWA Serious Violators"].loc[nj.results["SDWA Serious Violators"]["CITY_SERVED"]==pick_area.value]

# Display the results
if len(nj.results["SDWA Serious Violators"].index) > 0:
  display(nj.results["SDWA Serious Violators"][["PWS_NAME", "CITY_SERVED", "POPULATION_SERVED_COUNT", "FISCAL_YEAR", "SERIOUS_VIOLATOR"]])
else:
  display("There are no serious violators.")

This data has already been added!


PWS_NAME  ... SERIOUS_VIOLATOR
18  NJ AMERICAN WATER - SHORT HILLS  ...                Y
11           LAMINGTON SCHOOL HOUSE  ...                Y
12           LAMINGTON SCHOOL HOUSE  ...                Y
7        FIDDLERS ELBOW GOLF COURSE  ...                Y

[4 rows x 5 columns]

## Environmental Justice Analysis for this Area
Currently this examines ALL types of EPA-regulated facilities for the area selected above, not just PWS.

Start by collecting the data. This may take some time!

In [ ]:
# Get spatial data on Census-defined places (cities, townships, etc.) for New Jersey
import requests, zipfile, io
url = "https://www2.census.gov/geo/tiger/TIGER2021/PLACE/tl_2021_34_place.zip"
r = requests.get(url)
z = zipfile.ZipFile(io.BytesIO(r.content))
z.extractall("/content")
places = geopandas.read_file("/content/tl_2021_34_place.shp")

# Filter to the previously selected place
place_name = pick_area.value[:-10] # This cuts e.g. "BEDMINSTER TWP.-1801" to just "BEDMINSTER". It will work for most places in NJ, but not those without TWP.-####
place = places.loc[places["NAME"]==place_name.capitalize()]

# Get census blocks for this place
url = "https://www2.census.gov/geo/tiger/TIGER2010/TABBLOCK/2010/tl_2010_34_tabblock10.zip"
r = requests.get(url)
z = zipfile.ZipFile(io.BytesIO(r.content))
z.extractall("/content")
census_blocks = geopandas.read_file("/content/tl_2010_34_tabblock10.shp", mask = place)

# Get facilities by these Census_Blocks
f = geopandas.clip(nj.facilities, census_blocks)

print("Done!")

Next, we'll map these census blocks.

*   Red = blocks with ECHO facilities and are flagged by EPA's EJScreen environmental justice indicator
*   Yellow = blocks with ECHO facilities but not EJScreen flagged
*   Blue = all other blocks (no facilities)
*   Green outline = the city/place selected
*   Pins = facilities listed in ECHO that are in this city/place


In [37]:
# Show census blocks + EJ_SCREEN
place_cbs = list(census_blocks["GEOID10"].unique())
# CBs with facilities AND EJ_SCREEN FLAG
dump = f.loc[f['EJSCREEN_FLAG_US'] == "Y"]
dump = list(dump['FAC_DERIVED_CB2010'].unique())
dump = [str(int(x)) for x in dump if str(x) != 'nan']
cb_fac_ej = census_blocks.loc[census_blocks["GEOID10"].isin(dump)]
# CBs with facilities and not EJ_SCREEN
dump = f.loc[f['EJSCREEN_FLAG_US'] == "N"]
dump = list(dump['FAC_DERIVED_CB2010'].unique())
dump = [str(int(x)) for x in dump if str(x) != 'nan']
cb_fac_nej = census_blocks.loc[census_blocks["GEOID10"].isin(dump)]
# CBs with no facilities
other_cb = list( set(place_cbs).difference(set(list(cb_fac_ej['GEOID10'].unique()) + list(cb_fac_nej['GEOID10'].unique()))) )
other_cb = census_blocks.loc[census_blocks['GEOID10'].isin(other_cb)]

m = folium.Map()
style = {
    'ej': {'fillColor': 'red', 'fillOpacity': 1,'lineColor': 'red', 'weight': 2},
    'fac': {'fillColor': 'yellow', 'fillOpacity': 1,'lineColor': 'yellow', 'weight': 2},
    'other': {'fillColor': 'blue', 'fillOpacity': .5,'lineColor': 'blue', 'weight': 1},
    'place': {'fillColor': 'green', 'fillOpacity': 0, 'lineColor': 'green', 'weight': 3} 
    } 
p = folium.GeoJson(
  place,
  style_function = lambda x: style['place']
).add_to(m)

if len(other_cb) > 0:
  z = folium.GeoJson(
    other_cb,
    style_function = lambda x: style['other']
  ).add_to(m)

if len(cb_fac_nej) > 0:
  y = folium.GeoJson(
    cb_fac_nej,
    style_function = lambda x: style['fac']
  ).add_to(m)

if len(cb_fac_ej) > 0:
  x = folium.GeoJson(
    cb_fac_ej,
    style_function = lambda x: style['ej']
  ).add_to(m)

if len(f) > 0:
  z = folium.GeoJson(
    f
  ).add_to(m)

bounds = m.get_bounds()
m.fit_bounds(bounds, padding=0)

display(m)

## Analysis of State-wide EJ Trends

Test: whether communities served by serious violators tend to be more flagged by EJScreen than communities not served by serious violators

First, once again get all SDWA serious violators for the state of NJ. This may take a minute or two1

In [39]:
nj = Echo(['NJ'], "States", ["SDWA Serious Violators"])
nj.results["SDWA Serious Violators"]

783 program records were found


PWSID  ...                                            DFR_URL
0   NJ1615017  ...  http://echo.epa.gov/detailed-facility-report?f...
0   NJ1615381  ...  http://echo.epa.gov/detailed-facility-report?f...
1   NJ1615370  ...  http://echo.epa.gov/detailed-facility-report?f...
2   NJ1615438  ...  http://echo.epa.gov/detailed-facility-report?f...
3   NJ1615018  ...  http://echo.epa.gov/detailed-facility-report?f...
..        ...  ...                                                ...
1   NJ1007306  ...  http://echo.epa.gov/detailed-facility-report?f...
2   NJ1021434  ...  http://echo.epa.gov/detailed-facility-report?f...
3   NJ1007306  ...  http://echo.epa.gov/detailed-facility-report?f...
4   NJ1021412  ...  http://echo.epa.gov/detailed-facility-report?f...
5   NJ1022383  ...  http://echo.epa.gov/detailed-facility-report?f...

[783 rows x 30 columns]

As you can see, "serious violators" are defined per fiscal year. We'll filter the serious violators data to Fiscal Year 2021, the most recent available.

We'll match the "CITY_SERVED" column with a dataset on New Jersey municipal boundaries.

The output of this cell is the census blocks served by serious violators.

In [110]:
sv = nj.results["SDWA Serious Violators"]
sv21 = sv.loc[sv["FISCAL_YEAR"]==2021] # SVs in FY21

# Pull out places served and match with a file of NJ municipalities for mapping purposes.
# First, get a GeoJSON of NJ Municipalities
munis = geopandas.read_file("https://github.com/edgi-govdata-archiving/ECHO-Geo/raw/main/Municipal_Boundaries_of_NJ.json")

# Match places served with municipalities
idxs = []
city_served = list(sv21["CITY_SERVED"].unique())
city_served = [str(cs) for cs in city_served if cs != "nan"]
for position, row in munis.iterrows():
  for city in city_served:
    if row["MUN"].upper() in city:
      idxs.append(position) #Collect postition
munis = munis.loc[munis.index.isin(idxs)]

# Clip census blocks by filtered municipalities
census_blocks_served = geopandas.read_file("/content/tl_2010_34_tabblock10.shp", mask = munis)
census_blocks_served

STATEFP10  ...                                           geometry
0            34  ...  POLYGON ((-74.59636 39.55338, -74.59762 39.554...
1            34  ...  POLYGON ((-74.66029 39.51783, -74.65762 39.515...
2            34  ...  POLYGON ((-74.64657 39.50817, -74.64731 39.507...
3            34  ...  POLYGON ((-74.67433 39.52705, -74.67437 39.527...
4            34  ...  POLYGON ((-74.61600 39.53872, -74.61460 39.537...
...         ...  ...                                                ...
33985        34  ...  POLYGON ((-75.03271 40.88043, -75.03234 40.880...
33986        34  ...  POLYGON ((-75.09091 40.92479, -75.09085 40.924...
33987        34  ...  POLYGON ((-75.09766 40.93003, -75.09749 40.930...
33988        34  ...  POLYGON ((-75.09128 40.92751, -75.09148 40.927...
33989        34  ...  POLYGON ((-75.06682 40.95083, -75.06827 40.953...

[33990 rows x 16 columns]

Now we'll map the *places* served by serious violators (right now, mapping the census blocks may be too much for the notebook to bear as there are ~34,000+ blocks served by serious violators. We can still analyze these, just not map them.)

In [111]:
map = folium.Map()

c = folium.GeoJson(
  munis
).add_to(map)

bounds = map.get_bounds()
map.fit_bounds(bounds, padding=0)

display(map)

We'll compare the attributes of census blocks served by serious violators to census blocks not served by serious violators.

Are the PWS that serve majority White communities less likely to be serious violators?

In [108]:
# Download the # of Whites per Census Block
Whites = censusdata.download('sf1', 2010, censusdata.censusgeo([('state', '34'), 
  ('county', '*'), ('tract', '*'), ('block', '*')]), ['P005003', 'P001001', 'GEO_ID']) # Census Variable P005003 = Total!!Not Hispanic or Latino!!White alone
Whites["WHITE_PCT"] = (Whites['P005003']/Whites['P001001'] * 100)
Whites["GEOID10"] = Whites["GEO_ID"].str.slice(start=9)
Whites.reset_index(drop=True, inplace=True)
Whites.set_index("GEOID10", inplace=True)
Whites = Whites[["P005003", 'P001001', "WHITE_PCT"]]
Whites

P005003  P001001   WHITE_PCT
GEOID10                                      
340010001001000        0        0         NaN
340010001001001        0        0         NaN
340010001001002        0        0         NaN
340010001001003        0       25    0.000000
340010001001004        0        0         NaN
...                  ...      ...         ...
340410324002071        0        0         NaN
340410324002072        0        0         NaN
340410324002073        7        7  100.000000
340410324002074        9        9  100.000000
340410324002075       35       36   97.222222

[169588 rows x 3 columns]

In [112]:
# Merge with both sets of census blocks
census_blocks = geopandas.read_file("/content/tl_2010_34_tabblock10.shp")
census_blocks = census_blocks.merge(Whites, on="GEOID10")
census_blocks_served = census_blocks_served.merge(Whites, on="GEOID10")

# Calculate % White Across Blocks Served by Serious Violators vs Blocks Not Served by Serious Violators
census_blocks_pct = (census_blocks["P005003"].sum() / census_blocks["P001001"].sum()) *100
census_blocks_served_pct = (census_blocks_served["P005003"].sum() / census_blocks_served["P001001"].sum()) *100
print("% White in Blocks Not Served by Serious Violators:", census_blocks_pct)
print("% White in Blocks Served by Serious Violators:",census_blocks_served_pct)

Average % White in Blocks Not Served by Serious Violators: 59.3146141206889
Average % White in Blocks Served by Serious Violators: 64.73260765522384


This is just a first-cut analysis! Suggests problems with rural PWS, not identifying urban PWS as serious violators, etc. Indeed, most of the serious vilators are "very small" sized:

In [117]:
sv21.groupby(by="PWS_SIZE")[["PWSID"]].count()

PWSID
PWS_SIZE         
Large           5
Medium          4
Small          13
Very Large      2
Very Small     78